### Link to scrape makro product

In [2]:
webPath = 'https://www.makrocambodiaclick.com/en/'
r = requests.get(webPath)

# adding beautiful soup
soup = bs(r.content)

contents = soup.prettify()
print(contents)

NameError: name 'requests' is not defined

In [80]:
# import lib
from bs4 import BeautifulSoup as bs
import requests
import json
import re
from datetime import datetime
import pickle

## Load the webpage

In [11]:
r = requests.get('https://en.wikipedia.org/wiki/Toy_Story_3')

# adding beautiful soup
soup = bs(r.content)

contents = soup.prettify()
print(contents)

<!DOCTYPE html>
<html class="client-nojs" dir="ltr" lang="en">
 <head>
  <meta charset="utf-8"/>
  <title>
   Toy Story 3 - Wikipedia
  </title>
  <script>
   document.documentElement.className="client-js";RLCONF={"wgBreakFrames":false,"wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgRequestId":"a0d4dd3c-6db8-49ff-a126-0fc5791632fc","wgCSPNonce":false,"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":false,"wgNamespaceNumber":0,"wgPageName":"Toy_Story_3","wgTitle":"Toy Story 3","wgCurRevisionId":1084957594,"wgRevisionId":1084957594,"wgArticleId":1213838,"wgIsArticle":true,"wgIsRedirect":false,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["IMDb ID (Cite Mojo) different from Wikidata","Articles with short description","Short description matches Wikidata","Good articles","Wikipedi

In [12]:
info_box = soup.find(class_="infobox vevent")
info_rows = info_box.find_all("tr")
for row in info_rows:
    print(row.prettify())

<tr>
 <th class="infobox-above summary" colspan="2" style="font-size: 125%; font-style: italic;">
  Toy Story 3
 </th>
</tr>

<tr>
 <td class="infobox-image" colspan="2">
  <a class="image" href="/wiki/File:Toy_Story_3_poster.jpg" title="All of the toys packed close together, holding up a large numeral '3', with Buzz, who is putting a friendly arm around Woody's shoulder, and Woody holding the top of the 3.">
   <img alt="All of the toys packed close together, holding up a large numeral '3', with Buzz, who is putting a friendly arm around Woody's shoulder, and Woody holding the top of the 3." class="thumbborder" data-file-height="326" data-file-width="220" decoding="async" height="326" src="//upload.wikimedia.org/wikipedia/en/6/69/Toy_Story_3_poster.jpg" width="220"/>
  </a>
  <div class="infobox-caption">
   Theatrical release poster
  </div>
 </td>
</tr>

<tr>
 <th class="infobox-label" scope="row" style="white-space: nowrap; padding-right: 0.65em;">
  Directed by
 </th>
 <td class="

In [13]:
def get_content_value(row_data):
    if row_data.find("li"):
        return [li.get_text(" ", strip=True).replace('\xa0',' ') for li in row_data.find_all("li")]
    else:
        return row.find('td').get_text(" ", strip=True).replace('\xa0',' ')

movie_info = {}

for index, row in enumerate(info_rows):
    if index == 0:
        movie_info['title'] = row.find("th").get_text(" ", strip=True)
    elif index == 1:
        continue
    else:
        content_key = row.find('th').get_text(" ", strip=True)
        content_value = get_content_value(row.find('td'))
        movie_info[content_key] = content_value

    
(movie_info)

{'title': 'Toy Story 3',
 'Directed by': 'Lee Unkrich',
 'Screenplay by': 'Michael Arndt',
 'Story by': ['John Lasseter', 'Andrew Stanton', 'Lee Unkrich'],
 'Produced by': 'Darla K. Anderson',
 'Starring': ['Tom Hanks',
  'Tim Allen',
  'Joan Cusack',
  'Don Rickles',
  'Wallace Shawn',
  'John Ratzenberger',
  'Estelle Harris',
  'Ned Beatty',
  'Michael Keaton',
  'Jodi Benson',
  'John Morris'],
 'Cinematography': ['Jeremy Lasky', 'Kim White'],
 'Edited by': 'Ken Schretzmann',
 'Music by': 'Randy Newman',
 'Production companies': ['Walt Disney Pictures', 'Pixar Animation Studios'],
 'Distributed by': 'Walt Disney Studios Motion Pictures',
 'Release dates': ['June 12, 2010 ( 2010-06-12 ) ( Taormina Film Fest )',
  'June 18, 2010 ( 2010-06-18 ) (United States)'],
 'Running time': '103 minutes [1]',
 'Country': 'United States',
 'Language': 'English',
 'Budget': '$200 million [1]',
 'Box office': '$1.067 billion [1]'}

## Scraping from the main site https://en.wikipedia.org/wiki/List_of_Walt_Disney_Pictures_films

In [14]:
r = requests.get('https://en.wikipedia.org/wiki/List_of_Walt_Disney_Pictures_films')

# adding beautiful soup
soup = bs(r.content)

contents = soup.prettify()
print(contents)

<!DOCTYPE html>
<html class="client-nojs" dir="ltr" lang="en">
 <head>
  <meta charset="utf-8"/>
  <title>
   List of Walt Disney Pictures films - Wikipedia
  </title>
  <script>
   document.documentElement.className="client-js";RLCONF={"wgBreakFrames":false,"wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgRequestId":"5c725f78-82e8-465d-ac06-0cd509e21d5e","wgCSPNonce":false,"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":false,"wgNamespaceNumber":0,"wgPageName":"List_of_Walt_Disney_Pictures_films","wgTitle":"List of Walt Disney Pictures films","wgCurRevisionId":1085223766,"wgRevisionId":1085223766,"wgArticleId":1970335,"wgIsArticle":true,"wgIsRedirect":false,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Webarchive template wayback links","CS1 maint: url-status","Articles wit

In [15]:
movies = soup.select(".wikitable.sortable i")
len(movies)

562

In [86]:
def get_content_value(row_data):
    if row_data.find("li"):
        return [li.get_text(" ", strip=True).replace('\xa0',' ') for li in row_data.find_all("li")]
    elif row_data.find("br"):
        return [text for text in row_data.stripped_strings]
    else:
        return row_data.get_text(" ", strip=True).replace("\xa0", " ")


def clean_tags(soup):
#     print(soup)
    for tag in soup.find_all(["sup", "span"]):
        tag.decompose()

def get_info_box(url):

    r = requests.get(url)

    # adding beautiful soup
    soup = bs(r.content)
    
    info_box = soup.find(class_="infobox vevent")
    info_rows = info_box.find_all("tr")
    
    clean_tags(soup)

    movie_info = {}

    for index, row in enumerate(info_rows):
        if index == 0:
            movie_info['title'] = row.find("th").get_text(" ", strip=True)
        else:
            header = row.find("th")
            if header:
                content_key = row.find('th').get_text(" ", strip=True)
                content_value = get_content_value(row.find('td'))
                movie_info[content_key] = content_value
            
    return movie_info
    

In [87]:
get_info_box("https://en.wikipedia.org/wiki/The_Great_Locomotive_Chase")

{'title': 'The Great Locomotive Chase',
 'Directed by': 'Francis D. Lyon',
 'Written by': 'Lawrence Edward Watkin',
 'Produced by': ['Lawrence Edward Watkin', 'Walt Disney'],
 'Starring': ['Fess Parker',
  'Jeffrey Hunter',
  'John Lupton',
  'Jeff York',
  'Slim Pickens'],
 'Cinematography': 'Charles Boyle',
 'Edited by': 'Ellsworth Hoagland',
 'Music by': 'Paul J. Smith',
 'Production company': 'Walt Disney Productions',
 'Distributed by': 'Buena Vista Distribution',
 'Release date': 'June 8, 1956',
 'Running time': '85 minutes',
 'Country': 'United States',
 'Language': 'English',
 'Box office': '$1.7 million (US)'}

In [88]:
r = requests.get('https://en.wikipedia.org/wiki/List_of_Walt_Disney_Pictures_films')

# adding beautiful soup
soup = bs(r.content)

movies = soup.select(".wikitable.sortable i a")
print(len(movies))
base_path = "https://en.wikipedia.org/"
movie_info_list = []

for index, movie in enumerate(movies):
    try:
        path_to_movie = movie['href']
        full_path = base_path + path_to_movie
        title = movie['title']
        movie_info_list.append(get_info_box(full_path))

    except Exception as e:
        print(movie.get_text())
        print(e)
movie_info_list      

534
Zorro the Avenger
'NoneType' object has no attribute 'find'
The Sign of Zorro
'NoneType' object has no attribute 'find'
The Beatles: Get Back – The Rooftop Concert
'NoneType' object has no attribute 'find'
61
'NoneType' object has no attribute 'find_all'
All Night Long
'NoneType' object has no attribute 'find'
Keeper of the Lost Cities
'NoneType' object has no attribute 'find_all'
Muppet Man
'NoneType' object has no attribute 'find_all'
Sister Act 3
'NoneType' object has no attribute 'find'
The Thief
'NoneType' object has no attribute 'find_all'
Tom Sawyer
'NoneType' object has no attribute 'find_all'
Tower of Terror
'NoneType' object has no attribute 'find_all'
Tron: Ares
'NoneType' object has no attribute 'find'
FC Barcelona
'NoneType' object has no attribute 'find_all'
Young Woman and the Sea
'NoneType' object has no attribute 'find_all'


[{'title': 'Academy Award Review of',
  'Production company': 'Walt Disney Productions',
  'Distributed by': 'United Artists',
  'Release date': ['May 19, 1937'],
  'Running time': '41 minutes (74 minutes 1966 release)',
  'Country': 'United States',
  'Language': 'English',
  'Box office': '$45.472'},
 {'title': 'Snow White and the Seven Dwarfs',
  'Directed by': ['David Hand',
   'William Cottrell',
   'Wilfred Jackson',
   'Larry Morey',
   'Perce Pearce',
   'Ben Sharpsteen'],
  'Written by': ['Ted Sears',
   'Richard Creedon',
   'Otto Englander',
   'Dick Rickard',
   'Earl Hurd',
   'Merrill De Maris',
   'Dorothy Ann Blank',
   'Webb Smith'],
  'Based on': ['Snow White', 'by The', 'Brothers Grimm'],
  'Produced by': 'Walt Disney',
  'Starring': ['Adriana Caselotti',
   'Lucille La Verne',
   'Harry Stockwell',
   'Roy Atwell',
   'Pinto Colvig',
   'Otis Harlan',
   'Scotty Mattraw',
   'Billy Gilbert',
   'Eddie Collins',
   'Moroni Olsen',
   'Stuart Buchanan'],
  'Music by':

In [89]:
len(movie_info_list)

520

### Save/Reload Data in json 

In [7]:
def save_data(title, data):
    with open(title, 'w', encoding='utf-8') as f:
        json.dump(data, f, ensure_ascii=False, indent=3)

In [8]:
def load_data(title):
    with open(title,encoding='utf-8') as f:
        return json.load(f)

In [92]:
save_data("disney_movie_data_clean_v1.json", movie_info_list)

### Cleaning data

In [9]:
# loading our data that just saved
movie_list_info = load_data("disney_movie_data_clean_v1.json")

#### SUB TAKS
- ~~Clean up references [1]~~
- ~~Converting time to integer~~
- Converting datetime to datetime object
- ~~Splitting long string to list~~
- ~~Converting budget & Box office to numbers~~

#### Starting task
- Cleaning up references

In [97]:
movie_list_info

[{'title': 'Academy Award Review of',
  'Production company': 'Walt Disney Productions',
  'Distributed by': 'United Artists',
  'Release date': ['May 19, 1937'],
  'Running time': '41 minutes (74 minutes 1966 release)',
  'Country': 'United States',
  'Language': 'English',
  'Box office': '$45.472'},
 {'title': 'Snow White and the Seven Dwarfs',
  'Directed by': ['David Hand',
   'William Cottrell',
   'Wilfred Jackson',
   'Larry Morey',
   'Perce Pearce',
   'Ben Sharpsteen'],
  'Written by': ['Ted Sears',
   'Richard Creedon',
   'Otto Englander',
   'Dick Rickard',
   'Earl Hurd',
   'Merrill De Maris',
   'Dorothy Ann Blank',
   'Webb Smith'],
  'Based on': ['Snow White', 'by The', 'Brothers Grimm'],
  'Produced by': 'Walt Disney',
  'Starring': ['Adriana Caselotti',
   'Lucille La Verne',
   'Harry Stockwell',
   'Roy Atwell',
   'Pinto Colvig',
   'Otis Harlan',
   'Scotty Mattraw',
   'Billy Gilbert',
   'Eddie Collins',
   'Moroni Olsen',
   'Stuart Buchanan'],
  'Music by':

## - Converting datetime to datetime object


In [120]:
[movie.get('Running time (int)', 'N/A') for movie in movie_list_info]

[41,
 83,
 88,
 126,
 74,
 64,
 70,
 42,
 70,
 71,
 75,
 94,
 73,
 75,
 82,
 68,
 74,
 96,
 75,
 84,
 77,
 92,
 69,
 81,
 60,
 127,
 93,
 76,
 75,
 73,
 85,
 81,
 70,
 90,
 80,
 75,
 83,
 83,
 72,
 97,
 75,
 104,
 93,
 105,
 95,
 97,
 134,
 69,
 92,
 126,
 79,
 97,
 128,
 73,
 91,
 105,
 98,
 130,
 89,
 93,
 67,
 98,
 100,
 118,
 103,
 110,
 80,
 74,
 91,
 91,
 97,
 118,
 139,
 131,
 92,
 87,
 116,
 93,
 110,
 110,
 131,
 101,
 108,
 84,
 78,
 75,
 164,
 106,
 110,
 99,
 113,
 108,
 102,
 85,
 91,
 93,
 100,
 100,
 79,
 96,
 113,
 89,
 117,
 92,
 88,
 92,
 87,
 93,
 93,
 93,
 90,
 83,
 96,
 88,
 89,
 91,
 93,
 92,
 97,
 100,
 100,
 89,
 None,
 91,
 112,
 115,
 95,
 91,
 97,
 104,
 74,
 48,
 77,
 104,
 128,
 101,
 94,
 104,
 90,
 100,
 88,
 93,
 98,
 112,
 84,
 97,
 97,
 114,
 96,
 97,
 109,
 83,
 90,
 107,
 96,
 103,
 91,
 95,
 105,
 113,
 80,
 101,
 90,
 74,
 90,
 89,
 110,
 74,
 93,
 84,
 83,
 74,
 77,
 107,
 93,
 88,
 108,
 84,
 121,
 89,
 104,
 90,
 86,
 84,
 108,
 107,
 96,
 98,
 

In [118]:
def minutes_to_integer(running_time):
    if running_time == "N/A":
        return None
    if isinstance(running_time, list):
        return int(running_time[0].split(" ")[0])
    else:
        return int(running_time.split(" ")[0])

minutes_to_integer(["85 minutes","95 minutes"])

for movie in movie_list_info:
    movie['Running time (int)'] = minutes_to_integer(movie.get('Running time', 'N/A'))
    

In [119]:
movie_list_info

[{'title': 'Academy Award Review of',
  'Production company': 'Walt Disney Productions',
  'Distributed by': 'United Artists',
  'Release date': ['May 19, 1937'],
  'Running time': '41 minutes (74 minutes 1966 release)',
  'Country': 'United States',
  'Language': 'English',
  'Box office': '$45.472',
  'Running time (int)': 41},
 {'title': 'Snow White and the Seven Dwarfs',
  'Directed by': ['David Hand',
   'William Cottrell',
   'Wilfred Jackson',
   'Larry Morey',
   'Perce Pearce',
   'Ben Sharpsteen'],
  'Written by': ['Ted Sears',
   'Richard Creedon',
   'Otto Englander',
   'Dick Rickard',
   'Earl Hurd',
   'Merrill De Maris',
   'Dorothy Ann Blank',
   'Webb Smith'],
  'Based on': ['Snow White', 'by The', 'Brothers Grimm'],
  'Produced by': 'Walt Disney',
  'Starring': ['Adriana Caselotti',
   'Lucille La Verne',
   'Harry Stockwell',
   'Roy Atwell',
   'Pinto Colvig',
   'Otis Harlan',
   'Scotty Mattraw',
   'Billy Gilbert',
   'Eddie Collins',
   'Moroni Olsen',
   'Stua

## - Converting budget & Box office to numbers

In [30]:
[movie.get('Box office', 'N/A') for movie in movie_list_info]

['$45.472',
 '$418 million',
 '$164 million',
 '$76.4–$83.3 million (United States and Canada)',
 '$960,000 (worldwide rentals)',
 '>$1.3 million (est. United States/Canada rentals, 1941)',
 '$267.4 million',
 '$1.135 million (worldwide rentals)',
 '$799,000',
 '$3.355 million (worldwide rentals)',
 '$3.275 million (worldwide rentals)',
 '$65 million',
 '$3.165 million (worldwide rentals)',
 '$2.56 million (worldwide rentals)',
 '$3.7 million (U.S. rental) $575,000 (foreign rental)',
 '$1.625 million (worldwide rentals)',
 '$182 million',
 '$4,100,000 (worldwide rentals)',
 ['$2.4 million (1951, domestic)', '$3.5 million (1974, domestic)'],
 '$2.1 million (US rentals)',
 '$87.4 million (United States and Canada)',
 '$1 million (US)',
 '$2.6 million (US)',
 'N/A',
 '$1.75 million (US and Canadian rentals)',
 '$28.2 million',
 '$2,150,000 (US)',
 '$187 million',
 '$2.1 million (US)',
 '$1.6 million (US)',
 '$1.7 million (US)',
 'N/A',
 'N/A',
 '$2.75 million (US)',
 'N/A',
 '$1.75 millio

In [69]:
amounts = r"thousand|million|billion"
number = r"\d+(,\d{3})*\.*\d*"

word_re = rf"\${number}(-|\sto\s|–)?({number})?\s({amounts})"
value_re = rf"\${number}"

def word_to_value(word):
    value_dict = {"thousand": 1000, "million": 1000000, "billion": 1000000000}
    return value_dict[word]

def parse_word_syntax(string):
    value_string = re.search(number, string).group()
    value = float(value_string.replace(",",""))
    word = re.search(amounts, string,flags=re.I).group().lower()
    word_value = word_to_value(word)
    return value * word_value
    

def parse_value_syntax(string):
    value_string = re.search(number, string).group()
    value = float(value_string.replace(",",""))
    return value

def money_conversion(money):
    if money == "N/A":
        return None
    
    if isinstance(money, list):
        money = money[0]
    
    word_syntax = re.search(word_re, money, flags=re.I)
    value_syntax = re.search(value_re, money)
    
    if word_syntax:
        return parse_word_syntax(word_syntax.group())
    
    elif value_syntax: 
        return parse_value_syntax(value_syntax.group())
    
    else:
        return None

# print(money_conversion("$12.22 Millions"))

In [67]:
for movie in movie_list_info:
#     del movie['Budget (fload)']
#     del movie['Box office (fload)']
    movie['Budget (float)'] = money_conversion(movie.get('Budget', 'N/A'))
    movie['Box office (float)'] = money_conversion(movie.get('Box office', 'N/A'))


$45.472
$1.49 million
$418 million
$2.6 million
$164 million
$2.28 million
$76.4–$83.3 million (United States and Canada)
$600,000
$960,000 (worldwide rentals)
$950,000
>$1.3 million (est. United States/Canada rentals, 1941)
$858,000
$267.4 million
$1.135 million (worldwide rentals)
$788,000
$799,000
$3.355 million (worldwide rentals)
$1.35 million
$3.275 million (worldwide rentals)
$2.125 million
$65 million
$3.165 million (worldwide rentals)
$1.5 million
$2.56 million (worldwide rentals)
$1.5 million
$3.7 million (U.S. rental) $575,000 (foreign rental)
$1.625 million (worldwide rentals)
$2.2 million
$182 million
$1,800,000
$4,100,000 (worldwide rentals)
$3 million
$2.4 million (1951, domestic)
$2.1 million (US rentals)
$4 million
$87.4 million (United States and Canada)
$2 million
$1 million (US)
$300,000
$2.6 million (US)
$1.8 million
$1.75 million (US and Canadian rentals)
$5 million
$28.2 million
$2,150,000 (US)
$4 million
$187 million
$2.1 million (US)
$1.6 million (US)
$1.7 mill

In [71]:
movie_list_info

[{'title': 'Academy Award Review of',
  'Production company': 'Walt Disney Productions',
  'Distributed by': 'United Artists',
  'Release date': ['May 19, 1937'],
  'Running time': '41 minutes (74 minutes 1966 release)',
  'Country': 'United States',
  'Language': 'English',
  'Box office': '$45.472',
  'Budget (float)': None,
  'Box office (float)': 45.472},
 {'title': 'Snow White and the Seven Dwarfs',
  'Directed by': ['David Hand',
   'William Cottrell',
   'Wilfred Jackson',
   'Larry Morey',
   'Perce Pearce',
   'Ben Sharpsteen'],
  'Written by': ['Ted Sears',
   'Richard Creedon',
   'Otto Englander',
   'Dick Rickard',
   'Earl Hurd',
   'Merrill De Maris',
   'Dorothy Ann Blank',
   'Webb Smith'],
  'Based on': ['Snow White', 'by The', 'Brothers Grimm'],
  'Produced by': 'Walt Disney',
  'Starring': ['Adriana Caselotti',
   'Lucille La Verne',
   'Harry Stockwell',
   'Roy Atwell',
   'Pinto Colvig',
   'Otis Harlan',
   'Scotty Mattraw',
   'Billy Gilbert',
   'Eddie Collins

In [68]:
money_conversion(str(movie_list_info[-40]["Budget"]))

$120–150 million


120000000.0

### - Converting datetime to datetime object

In [76]:
dates = [movie.get('Release date','N/A') for movie in movie_list_info]

def clean_date(date):
    return date.split('(')[0].strip()


def date_conversion(date):
    if isinstance(date,list):
        date = date[0]
    
    date_str = clean_date(date)
    
    if date_str == 'N/A':
        return None
    
    print(date_str)
    datetime_formates = ['%B %d, %Y', '%d %B %Y']
    for datetime_formate in datetime_formates:
        try:
            return datetime.strptime(date_str, datetime_formate)
        except:
            pass

        
    return None
    
    

May 19, 1937
1937-05-19 00:00:00

None

None

November 13, 1940
1940-11-13 00:00:00

June 27, 1941
1941-06-27 00:00:00

None

None

None

July 17, 1943
1943-07-17 00:00:00

None

None

None

September 27, 1947
1947-09-27 00:00:00

May 27, 1948
1948-05-27 00:00:00

None

October 5, 1949
1949-10-05 00:00:00

None

None

None

None

February 5, 1953
1953-02-05 00:00:00

July 23, 1953
1953-07-23 00:00:00

November 10, 1953
1953-11-10 00:00:00

None

August 17, 1954
1954-08-17 00:00:00

December 23, 1954
1954-12-23 00:00:00

May 25, 1955
1955-05-25 00:00:00

June 22, 1955
1955-06-22 00:00:00

September 14, 1955
1955-09-14 00:00:00

December 22, 1955
1955-12-22 00:00:00

June 8, 1956
1956-06-08 00:00:00

July 18, 1956
1956-07-18 00:00:00

September 4, 1956
1956-09-04 00:00:00

December 20, 1956
1956-12-20 00:00:00

June 19, 1957
1957-06-19 00:00:00

August 28, 1957
1957-08-28 00:00:00

December 25, 1957
1957-12-25 00:00:00

July 8, 1958
1958-07-08 00:00:00

August 12, 1958
1958-08-12 00:00:0

In [78]:
for movie in movie_list_info:
    movie['Release date (datetime)'] = date_conversion(movie.get('Release date','N/A'))

May 19, 1937
November 13, 1940
June 27, 1941
July 17, 1943
September 27, 1947
May 27, 1948
October 5, 1949
February 5, 1953
July 23, 1953
November 10, 1953
August 17, 1954
December 23, 1954
May 25, 1955
June 22, 1955
September 14, 1955
December 22, 1955
June 8, 1956
July 18, 1956
September 4, 1956
December 20, 1956
June 19, 1957
August 28, 1957
December 25, 1957
July 8, 1958
August 12, 1958
December 25, 1958
January 29, 1959
March 19, 1959
November 10, 1959
January 21, 1960
February 24, 1960
May 19, 1960
November 1, 1960
December 21, 1960
January 25, 1961
March 16, 1961
June 21, 1961
July 12, 1961
July 17, 1961
December 14, 1961
April 5, 1962
May 17, 1962
June 6, 1962
September 26, 1962
November 7, 1962
January 16, 1963
March 29, 1963
June 1, 1963
July 7, 1963
November 20, 1963
December 25, 1963
March 12, 1964
February 11, 1964
July 2, 1964
November 10, 1964
December 18, 1964
August 18, 1965
December 2, 1965
October 1, 1966
December 1, 1966
February 8, 1967
June 15, 1967
July 12, 1967


In [79]:
movie_list_info[50]

{'title': '101 Dalmatians',
 'Directed by': ['Clyde Geronimi', 'Hamilton Luske', 'Wolfgang Reitherman'],
 'Story by': 'Bill Peet',
 'Based on': ['The Hundred and One Dalmatians', 'by', 'Dodie Smith'],
 'Produced by': 'Walt Disney',
 'Starring': ['Rod Taylor',
  'Cate Bauer',
  'Betty Lou Gerson',
  'Ben Wright',
  'Bill Lee (singing voice)',
  'Lisa Davis',
  'Martha Wentworth'],
 'Edited by': ['Roy M. Brewer, Jr.', 'Donald Halliday'],
 'Music by': 'George Bruns',
 'Production company': 'Walt Disney Productions',
 'Distributed by': 'Buena Vista Distribution',
 'Release date': ['January 25, 1961'],
 'Running time': '79 minutes',
 'Country': 'United States',
 'Language': 'English',
 'Budget': '$3.6 million',
 'Box office': '$303 million',
 'Budget (float)': 3600000.0,
 'Box office (float)': 303000000.0,
 'Release date (datetime)': datetime.datetime(1961, 1, 25, 0, 0)}

In [81]:
### Saving data to pickle

In [87]:
name = 'disney_movie_data_clean_pickle_v1.pickle'
def save_data_pickle(name,data):
    with open(name, 'wb') as f:
        pickle.dump(data,f)
def load_data_pickle(name):
    with open(name, 'rb') as f:
        return pickle.load(f)

In [88]:
save_data_pickle(name, movie_list_info)

## Attach IMDB/Rotten Tomatoes scores

In [91]:
movie_list_info = load_data_pickle(name)